In [1]:
import urllib.request, json
import pandas as pd
import argparse
import numpy as np
from influxdb import InfluxDBClient

In [2]:
with urllib.request.urlopen("https://data.cdc.gov/api/views/bi63-dtpu/rows.json?accessType=DOWNLOAD") as url:data = json.loads(url.read().decode())
print(data)

{'meta': {'view': {'id': 'bi63-dtpu', 'name': 'NCHS - Leading Causes of Death: United States', 'attribution': 'National Center for Health Statistics', 'averageRating': 0, 'category': 'NCHS', 'createdAt': 1449080633, 'description': 'This dataset presents the age-adjusted death rates for the 10 leading causes of death in the United States beginning in 1999.\r\n\r\nData are based on information from all resident death certificates filed in the 50 states and the District of Columbia using demographic and medical characteristics. Age-adjusted death rates (per 100,000 population) are based on the 2000 U.S. standard population. Populations used for computing death rates after 2010 are postcensal estimates based on the 2010 census, estimated as of July 1, 2010. Rates for census years are based on populations enumerated in the corresponding censuses. Rates for non-census years before 2010 are revised using updated intercensal population estimates and may differ from rates previously published.\

In [3]:
parsed= data['data']
print(parsed)

[[1, '3DF698B2-EBEE-47BC-9B4C-AC5EA353093D', 1, 1503517372, '1018980', 1503517372, '1018980', None, '1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Alabama', '2313', '52.2'], [2, 'E4238B0C-1DB2-48E9-B371-429721E56917', 2, 1503517372, '1018980', 1503517372, '1018980', None, '1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Alaska', '294', '55.9'], [3, '4A0D624B-A840-4380-9D5A-05CDCEE2B191', 3, 1503517372, '1018980', 1503517372, '1018980', None, '1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Arizona', '2214', '44.8'], [4, 'C38B03CE-CC7B-4EA8-AE76-7FB5C0903E25', 4, 1503517372, '1018980', 1503517372, '1018980', None, '1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Arkansas', '1287', '47.6'], [5, 'EC50D847-D2C2-41CA-80BF-9F53DEE4F99A', 5, 1503517372, '1018980', 1503517372, '1018980', None, '1999', 'Accidents (unintentional

In [4]:
fined=[]
for i in parsed:
    fined.append(i[8:])
print(fined)

[['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Alabama', '2313', '52.2'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Alaska', '294', '55.9'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Arizona', '2214', '44.8'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Arkansas', '1287', '47.6'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'California', '9198', '28.7'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Colorado', '1519', '39'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Connecticut', '1034', '29.3'], ['1999', 'Accidents (unintentional injuries) (V01-X59,Y85-Y86)', 'Unintentional Injuries', 'Delaware', '267', '35.3'], ['1999', 'Accidents (unintentional injurie

In [5]:
df=pd.DataFrame(fined, columns=["Year", "113 Cause Name", "Cause Name", "State", "Deaths", "Age-adjusted Death Rate"])
print(df)

       Year                                     113 Cause Name  \
0      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
1      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
2      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
3      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
4      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
5      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
6      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
7      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
8      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
9      1999  Accidents (unintentional injuries) (V01-X59,Y8...   
10     1999  Accidents (unintentional injuries) (V01-X59,Y8...   
11     1999  Accidents (unintentional injuries) (V01-X59,Y8...   
12     1999  Accidents (unintentional injuries) (V01-X59,Y8...   
13     1999  Accidents (unintentional injuries) (V01-X59,Y8...   
14     199

In [6]:
df.to_csv("deaths.csv",index=False)

In [9]:
brics = pd.read_csv("C:/Users/Swarupa/Desktop/deaths.csv", index_col=0);

#print(brics)
def read_data():
    with open('C:/Users/Swarupa/Desktop/deaths.csv') as f: #Input the name of your csv file here
        return [x.split(',') for x in f.readlines()[1:]]
def read_header():
    with open('C:/Users/Swarupa/Desktop/deaths.csv') as f: #Input the name of your csv file here
        return [x.split(',') for x in f.readlines()[:1]]

def main(host='localhost', port=8086):       #input your port number which has been set for influx
    """Instantiate the connection to the InfluxDB client."""
    user = 'Swarupa'
    password = ''
    dbname = 'SocialWeather'
    # Temporarily avoid line protocol time conversion issues #412, #426, #431.
    protocol = 'json'

    client = InfluxDBClient(host, port, user, password, dbname)

    print("Create DataFrame");
    b=read_header();
    length=len(b);
    print(b);
    narr=(b[-1])
    narr[-1]=narr[-1].split('\n',1)[0]
    print(narr); # getting /n (new line?,why?)
    print("Create database: " + dbname)
    client.create_database(dbname)
    a = read_data();
    for metric in a:
        influx_metric = [{
            'measurement': 'Leading_Causes_Of_Deaths',
            'tags': {
                'State': metric[3]
            },
            'time':str(metric[0])+"-12-31"+"T00:00:00Z",
            'fields': {
                '113_Cause_Name': metric[1].strip(' ')[0],
                'Cause_Name': metric[2],
                'Deaths': metric[4],
                'Age-adjusted_Death_Rate': metric[5],
            }
        }]
        client.write_points(influx_metric)

    print("Read DataFrame")
    print(client.query("select * from Leading_Causes_Of_Deaths")) # all values are now without /n
    
if __name__ == '__main__':
    main()

Create DataFrame
[['Year', '113 Cause Name', 'Cause Name', 'State', 'Deaths', 'Age-adjusted Death Rate\n']]
['Year', '113 Cause Name', 'Cause Name', 'State', 'Deaths', 'Age-adjusted Death Rate']
Create database: SocialWeather
Read DataFrame
ResultSet({'('Leading_Causes_Of_Deaths', None)': [{'time': '1999-12-31T00:00:00Z', '113_Cause_Name': '"', 'Age-adjusted_Death_Rate': '258', 'Cause_Name': 'Y85-Y86)"', 'Deaths': 'Wyoming', 'State': 'Unintentional Injuries'}, {'time': '1999-12-31T00:00:00Z', '113_Cause_Name': '"', 'Age-adjusted_Death_Rate': '49', 'Cause_Name': 'K73-K74)"', 'Deaths': 'Wyoming', 'State': 'Chronic liver disease and cirrhosis'}, {'time': '1999-12-31T00:00:00Z', '113_Cause_Name': '"', 'Age-adjusted_Death_Rate': 'Diseases of Heart', 'Cause_Name': 'I11', 'Deaths': 'I20-I51)"', 'State': 'I13'}, {'time': '1999-12-31T00:00:00Z', '113_Cause_Name': '"', 'Age-adjusted_Death_Rate': 'Kidney Disease', 'Cause_Name': ' nephrotic syndrome and nephrosis (N00-N07', 'Deaths': 'N25-N27)"', 

In [ ]:
#Done